In [1]:
#find folders containing stack time series data and convert to HDF5
import pandas as pd
import pathlibDB as pldb
from pathlib import Path
import ccModules as cc
import pathlib

/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/CircuitCatcher2/tifffile.py:265: UserWarning: failed to import the optional _tifffile C extension module.
Loading of some compressed images will be very slow.
Tifffile.c can be obtained at http://www.lfd.uci.edu/~gohlke/
  "failed to import the optional _tifffile C extension module.\n"


In [2]:
targetfolder = str(Path.cwd().parent)
#targetfolder = pathlib.Path.cwd().parents[0]

MIP_str = 'MIP.hdf5'
Time_str = 'TimeSeries.hdf5'
print('Targetfolder :', targetfolder)

Targetfolder : /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97


In [3]:
files = pldb.getDirContents(targetfolder)

In [4]:
files = files[files['Directory'] == True]
files = files[(files['File_Name'].str.contains('stim30s06V')) | (files['File_Name'].str.contains('stimDur300at15'))]
print(files['File_Name'].values)

['flyb_20190624-A97-8_stimDur300at15_00001'
 'flyg_20190624-A97-8_stim30s06V_00001'
 'flya_20190624-A97-8_stimDur300at15_00001'
 'flya_20190624-A97-8_stim30s06V_00001'
 'flyf_20190624-A97-8_stimDur300at15_00001'
 'flyc_20190624-A97-8_stimDur300at15_00001'
 'flyg_20190624-A97-8_stimDur300at15_00001'
 'flyc_20190624-A97-8_stim30s06V_00001'
 'flyf_20190624-A97-8_stim30s06V_00001'
 'flyb_20190624-A97-8_stim30s06V_00001'
 'flye_20190624-A97-11_stim30s06V_00001'
 'flyk_20190529-A97-6_stim30s06V_00001_gpuregression1559219844'
 'flyd_20190529-A97-2_stim30s06V_00001'
 'flyi_20190529-A97-5_stim30s06V_stimDur300at15_00001_gpuregression1559220002'
 'flye_20190529-A97-3_stim30s06V_stim30s06V_00001'
 'flyh_20190529-A97-4_stim30s06V_00001_gpuregression1559220125'
 'flyb_20190529-A97-1_stimDur300at15_00001'
 'flyh_20190529-A97-4_stim30s06V_00001'
 'flyj_20190529-A97-5_stim30s06V_00001'
 'flye_20190529-A97-3_stim30s06V_1040nm_z_00001_gpuregression1559220330'
 'flyc_20190529-A97-2_stim30s06V_00001_gpure

In [6]:
#get and count the number of tif files in each folder
tif_files = []
tif_count = []
Time_count =[]
MIP_count =[]
for row, dseries in files.iterrows():
    tif = [str(i.parts[-1]) for i in Path(dseries['Full_Path']).glob('*.tif')]
    tif_files.append(tif)
    tif_count.append(len(tif))
    Time = [str(i.parts[-1]) for i in Path(dseries['Full_Path']).glob('*'+Time_str)]
    MIP = [str(i.parts[-1]) for i in Path(dseries['Full_Path']).glob('*'+MIP_str)]
    Time_count.append(len(Time))
    MIP_count.append(len(MIP))
files['tif_count'] = tif_count
files['tif_files'] = tif_files
files['TimeSeries_count'] = Time_count
files['MIP_count'] = MIP_count
files = files[files['tif_count'] > 10]
#remove folders that already have both MIP and Timeseries data
files = files[(files['MIP_count'] == 0) | (files['TimeSeries_count'] == 0)]
files= files[~files['File_Name'].str.contains('1040nm')]


In [7]:
time_path = []
MIP_path = []
for row, dseries in files.iterrows():
    time_path.append(str(Path(dseries['Full_Path']) / str( dseries['File_Name'] + Time_str)))
    MIP_path.append(str(Path(dseries['Full_Path']) / str( dseries['File_Name'] + MIP_str)))
files['TimeSeries_Output_HDF5'] = time_path
files['MIP_Output_HDF5'] = MIP_path
files.to_excel(str(Path(targetfolder) / 'GenerateTimeSeriesImages.xlsx'))

In [8]:
#for troubleshooting
'''
row = files[files['File_Name'].str.contains('flyc_20190617-A99-3_LED-06_Interval-31_00001')]
dseries = row.iloc[0]
type(dseries)
cc.generateHDFfromStackedTimeSeries(dseries['TimeSeries_Output_HDF5'], dseries['MIP_Output_HDF5'], dseries['Full_Path'], dseries['tif_files'])
'''

"\nrow = files[files['File_Name'].str.contains('flyc_20190617-A99-3_LED-06_Interval-31_00001')]\ndseries = row.iloc[0]\ntype(dseries)\ncc.generateHDFfromStackedTimeSeries(dseries['TimeSeries_Output_HDF5'], dseries['MIP_Output_HDF5'], dseries['Full_Path'], dseries['tif_files'])\n"

In [9]:
print('Starting to convert timeseries data.')
for row, dseries in files.iterrows():
    print('Starting :' , dseries['Full_Path'])
    cc.generateHDFfromStackedTimeSeries(dseries['TimeSeries_Output_HDF5'], dseries['MIP_Output_HDF5'], dseries['Full_Path'], dseries['tif_files'])
print('Finished converting Tif files to HDF5.')

Starting to convert timeseries data.
Starting : /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190529/flyk_20190529-A97-6_stimDur300at15_00001


/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary par

Starting : /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190529/flyh_20190529-A97-4_stimDur300at15_00001


/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary par

Starting : /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190529/flyk_20190529-A97-6_stim30s06V_00001


...

Starting : /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190508/flyf_20190508-A97-3_stim30s06V_00001


/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary par

Starting : /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190508/flyk_20190508-A97-6_stimDur300at15_00001


/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary part
  nparr = numpy.array(nparr, dtype=atom.dtype, copy=copy)
/groups/projtechres/home/busheyd/.local/share/virtualenvs/CircuitCatcher2-WgyRvAAM/lib/python3.7/site-packages/tables/utils.py:101: ComplexWarning: Casting complex values to real discards the imaginary par

Finished converting Tif files to HDF5.


In [17]:
print('Finding folders with both TimeSeries.hdf5 and MIP.hdf5 to move tif files to archive.')
files = pldb.getDirContents(targetfolder)
files = files[files['Directory'] == True]
files = files[(files['File_Name'].str.contains('stim30s06V')) | (files['File_Name'].str.contains('stimDur300at15'))]
#get and count the number of tif files in each folder
tif_files = []
tif_count = []
Time_count =[]
MIP_count =[]
for row, dseries in files.iterrows():
    tif = [str(i.parts[-1]) for i in Path(dseries['Full_Path']).glob('*.tif')]
    tif_files.append(tif)
    tif_count.append(len(tif))
    Time = [str(i.parts[-1]) for i in Path(dseries['Full_Path']).glob('*'+Time_str)]
    MIP = [str(i.parts[-1]) for i in Path(dseries['Full_Path']).glob('*'+MIP_str)]
    Time_count.append(len(Time))
    MIP_count.append(len(MIP))
files['tif_count'] = tif_count
files['tif_files'] = tif_files
files['TimeSeries_count'] = Time_count
files['MIP_count'] = MIP_count
files = files[files['tif_count'] > 10]
#remove folders that already have both MIP and Timeseries data
files = files[(files['MIP_count'] == 1) & (files['TimeSeries_count'] == 1)]
files= files[~files['File_Name'].str.contains('1040nm')]
print(files['Full_Path'].values)

Finding folders with both TimeSeries.hdf5 and MIP.hdf5 to move tif files to archive.
['/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyb_20190624-A97-8_stimDur300at15_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyg_20190624-A97-8_stim30s06V_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flya_20190624-A97-8_stimDur300at15_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flya_20190624-A97-8_stim30s06V_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyf_20190624-A97-8_stimDur300at15_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyc_20190624-A97-8_stimDur300at15_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyg_20190624-A97-8_stimDur300at15_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyc_20190624-A97-8_stim30s06V_00001'
 '/run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyf_2

In [18]:
print('Starting to move tif files to an archive folder.')
for row, dseries in files.iterrows():
    #make archive folder
    print('Moving : ', dseries['Full_Path'])
    outputfolder = Path(dseries['Full_Path']) / 'Archive'
    if not outputfolder.is_dir():
        outputfolder.mkdir()
    #transfer tif to archive folder
    for ctif in dseries['tif_files']:
        cpath = Path(dseries['Full_Path']) / ctif
        cpath.replace(outputfolder / ctif)
print('Finished archiving the tif files.')

Starting to move tif files to an archive folder.
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyb_20190624-A97-8_stimDur300at15_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyg_20190624-A97-8_stim30s06V_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flya_20190624-A97-8_stimDur300at15_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flya_20190624-A97-8_stim30s06V_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyf_20190624-A97-8_stimDur300at15_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyc_20190624-A97-8_stimDur300at15_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyg_20190624-A97-8_stimDur300at15_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupPlusDrive/A97/20190624/flyc_20190624-A97-8_stim30s06V_00001
Moving :  /run/media/busheyd/Backup2/SeagateBackupP